Puzzle and data description can be found here: https://adventofcode.com/2020/day/7

In [1]:
from typing import Tuple, List
import math

import numpy as np

import plotly.graph_objects as go
import plotly.io as pio
pio.templates.default = 'plotly_white'
import bezier
from webcolors import name_to_rgb 
from colorsys import rgb_to_hsv

from aocd import get_data

from solution import get_rules_map

from dotenv import load_dotenv
load_dotenv()

True

In [2]:
data = get_data(day=7, year=2020)
rules_map = get_rules_map(data)

Rules map is a dict with outer bag colors as keys and inner bags as values, where inner bags itself is a dict with inner bag colors as keys and required number of bags as values, i.e. line

`shiny gold bags contain 1 dark olive bag, 2 vibrant plum bags.`

from data becomes

`{'shiny gold': {'dark olive': 1, 'vibrant plum': 2}}`

The **goal is to visualize these relationships as a chord diagram**, drawing a line from each outer bag to inner bag with required number of bags as the width of the line. 

Extract nodes and edges from rules map:

In [3]:
edges = [(outer, inner, count) 
         for outer, inner_bags in rules_map.items() 
         for inner, count in inner_bags.items()]

node_names = list({bag for edge in edges for bag in edge[:2]})

Get colors in HSV code in order to sort nodes by color:

In [4]:
def get_node_hsv_color_from_name(node: str) -> Tuple[float, float, float]:
    shade, color = node.split(' ')
    
    try:
        rgb = name_to_rgb(shade + color)
    except ValueError:
        try:
            rgb = name_to_rgb(color)
        except ValueError:
            rgb = name_to_rgb('white')
            
    r, g, b = np.array(rgb) / 255
    return rgb_to_hsv(r, g, b)

In [5]:
node_hsv_colors = [get_node_hsv_color_from_name(name) for name in node_names]

node_names, node_hsv_colors = zip(
    *sorted(
        zip(node_names, node_hsv_colors), 
        key=lambda name_hsv: name_hsv[1]
    )
)

Convert HSV codes to HSV string for plotly:

In [6]:
def get_hsv_string_from_hsv(hsv: Tuple[float, float, float]) -> str:
    h, s, v = hsv
    return f'hsv({h*360:.0f},{s:.0%},{v:.0%})'

In [7]:
node_colors = [get_hsv_string_from_hsv(hsv) for hsv in node_hsv_colors]

Find x and y coordinates for nodes along a circle:

In [8]:
def get_points_on_unit_circle(n: int) -> List[Tuple[float, float]]:
    return [(math.cos(2 * math.pi * i / n), math.sin(2 * math.pi * i / n)) for i in range(0, n)]

In [9]:
node_coordinates = get_points_on_unit_circle(len(node_names))
x, y = zip(*node_coordinates)

In [10]:
fig = go.Figure(
    layout=go.Layout(
        title='',
        xaxis=dict(
            showgrid=False,
            zeroline=False,
            showticklabels=False
        ),
        yaxis=dict(
            scaleanchor="x", 
            scaleratio=1,
            showgrid=False,
            zeroline=False,
            showticklabels=False
        ),
        showlegend=False,
        height=800
    )
)

for source, target, count in edges:
    i_s, i_t = node_names.index(source), node_names.index(target)
    x_s, y_s = x[i_s], y[i_s]
    x_t, y_t = x[i_t], y[i_t]
    
    curve = bezier.Curve([[x_s, 0, x_t], [y_s, 0, y_t]], degree=2)
    curve_x, curve_y = curve.evaluate_multi(np.linspace(0, 1, 20))    
    
    fig.add_trace(
        go.Scatter(
            x=curve_x,
            y=curve_y,
            mode='lines',
            line=dict(
                width=count,
                color=node_colors[i_s]
            ),
            opacity=0.1,
            hovertemplate=f'{source} bags contain {count} {target} {"bag" if count == 1 else "bags"}<extra></extra>'
        )
    )

fig.add_trace(
    go.Scatter(
        x=x,
        y=y,
        text=node_names,
        hovertemplate='%{text}<extra></extra>',
        mode='markers',
        marker=dict(
            size=10,
            color=node_colors
        )
    )
)

fig.show()